In [651]:
#!/usr/bin/python
# -*- coding: UTF-8 -*-
import os
import sys
from bs4 import BeautifulSoup
import re
import shutil
import pandas as pd

if __name__ == "__main__":
    if len(sys.argv) > 0:
        fname = sys.argv[0]
    else:
        fname = "EdgarFillings_full/Form10K/1467858/1467858_10-K_2017-02-07_0001467858-17-000028.txt"
    print('Input file: ', fname)
    output_path = 'output/'
    segments = splitTextFile(fname, output_path)

AttributeError: 'list' object has no attribute 'shape'

In [649]:
def extractPage(page, idx_body, idx_page, path):
    soup = BeautifulSoup(page, "lxml")
    if soup.body:
        soup = soup.body

    for i, table in enumerate(soup.find_all('table')):
        df = readTable(table)
        fname = 'table%03d_body%03d-page%03d.txt' % (i, idx_body, idx_page)
        with open(path + fname, 'w') as f:
            print('--Write table: ', i, ' to csv.')
            df.to_csv(f)
        table.extract()

    text = '\n'.join(list(soup.stripped_strings))
    fname = 'text_body%03d-page%03d.txt' % (idx_body, idx_page)
    with open(path + fname, 'w') as f:
        print('--Write text file.')
        f.write(text)

In [639]:
def splitTextFile(fname, path):
    # check if output dir exists
    if os.path.exists(path):
        shutil.rmtree(path)
        os.mkdir(path)
        
    # read original data file  
    with open(fname, 'r', encoding='utf-8') as f:
        source_code = f.read()
    pattern = re.compile('[\r\n\t]')
    html = pattern.sub('', source_code) 
    
    # split html by 'body'
    bodys = re.findall('<body.*?</body>', html)
    
    # split body to pages by horizontal line
    segments = []
    for i, body in enumerate(bodys):
        pages = re.split('<hr.*?>', body)
        segments.append(pages)
        for j, page in enumerate(pages):
            filename = path + 'body%03d-page%03d.html' % (i, j)
            print('Write file: ', filename)
            with open(filename, 'w') as f:
                f.write(page)
                
            # extract information from page
            extractPage(page, i, j, path)
        
    return(segments)

In [654]:
fname = "EdgarFillings_full/Form10K/1467858/1467858_10-K_2017-02-07_0001467858-17-000028.txt"
with open(fname, 'r', encoding='utf-8') as f:
    source_code = f.read()
pattern = re.compile('[\r\n\t]')
html = pattern.sub('', source_code) 
bodys = re.findall('<body.*?</body>', html)

bodys[0]

'<body style="font-family:Times New Roman;font-size:10pt;"><div><a name="sC90F5628251B5422B3C1206467BE1EC7"></a></div><div><div style="line-height:120%;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;"><br></font></div><div style="line-height:120%;font-size:10pt;"><a style="font-family:inherit;font-size:10pt;" href="#s13D5A678946F5990A3E3DEC0801724E2"><font style="font-family:inherit;font-size:10pt;">Table of Contents</font></a></div><div style="line-height:120%;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;"><br></font></div></div><div><br></div><div style="line-height:120%;padding-top:6px;text-align:center;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;font-weight:bold;">UNITED STATES SECURITIES AND EXCHANGE COMMISSION</font></div><div style="line-height:120%;text-align:center;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;font-weight:bold;">Washington, DC 20549-1004</font></div><div style="line-height:120%;paddi

In [655]:
for i, body in enumerate(bodys):
    print(i, len(body))

0 4426766
1 59235
2 133618
3 4155
4 3369
5 113781
6 11291
7 11344
8 10306
9 527732
10 27272
11 66066
12 20747
13 102947
14 5820
15 88599
16 46081
17 9056
18 70516
19 7383
20 72950
21 111876
22 43295
23 46989
24 142325
25 43963
26 37137
27 23487
28 52973
29 112972
30 513558
31 74127
32 144359
33 32654
34 17585
35 61893
36 47480
37 31434
38 63390
39 459547
40 42765
41 10277
42 130122
43 258882
44 111435
45 43784
46 47058
47 147756
48 41084
49 31512
50 26378
51 53420
52 93656
53 776724
54 28192
55 142352
56 22412
57 17402
58 49498
59 46014
60 19016
61 60106
62 454338
63 41220
64 95956
65 27631
66 59911
67 29389
68 19301
69 33403
70 19744
71 20053
72 36951
73 57124
74 40861
75 20436
76 46795
77 8297
78 34492
79 22622
80 33748
81 19049
82 39364
83 18629
84 189477
85 31787
86 37515
87 22804
88 85316
89 23640
90 60317
91 17743
92 83049
93 54031
94 65304
95 41804
96 73514
97 41609
98 21173
99 55536
100 9389
101 26390
102 15813
103 33662
104 36025
105 54649
106 56165
107 196004
108 34438
109 27

In [613]:
def readTable(table):
    matrix = []
    if table.th:
        data = []
        for j, col in enumerate(table.th.find_all('td')):
            data.append(''.join(list(col.stripped_strings)))
        matrix.append(data)

    for i, row in enumerate(table.find_all('tr')):
        data = []
        for j, col in enumerate(row.find_all('td')):
            data.append(''.join(list(col.stripped_strings)))

        matrix.append(data)
    return(pd.DataFrame(matrix))


In [328]:
def readIndexTable(tables):
    df = pd.DataFrame(columns=('part', 'item', 'title', 'page', 'ref'))

    rows = tables[0].find_all('tr')
    curPart = ""
    n = 0
    for i, row in enumerate(rows):
        cols = row.find_all('td')
        l = len(cols)
        if cols[0].string is None or (l > 1 and cols[1].string == '\xa0'): 
            continue
        elif cols[0].string.startswith('PART'):
            curPart = cols[0].string
            continue      
        data = []
        data.append(curPart)
        data.append(cols[0].string)
        if l > 3:
            data.append(cols[1].string + cols[2].string)
            data.append(cols[3].string)
        else:
            data.append(cols[1].string)
            data.append(cols[2].string)
        data.append(cols[l-1].a.get('href'))
        #print(i, data)
        #cols.append(cols[l-1].a.get('href'))
        df.loc[n] = data
        n += 1
        return(df)

In [540]:
def readDiv(content, concate=True):
    #print(content)
    tags_table = [] 
    tags_a = []
    tags_font = []
    for cnt in content.children:
        if cnt.find('div', recursive=False):
            tag_table, tag_a, tag_font = readDiv(cnt)
            tags_table.extend(tag_table)
            tags_a.extend(tag_a)
            tags_font.extend(tag_font)

            #print(tag_font)
        elif cnt.name == 'table': 
            print('table')
            #readTable(cnt)
        elif cnt.name == 'a':
            tag_a, tag_font = readContent(cnt)
            tags_a.extend(tag_a)
            if concate:
                tags_font.append(' '.join(tag_font))
            else:
                tags_font.extend(tag_font)

    return(tags_table, tags_a, tags_font)

In [427]:
def readContent(div):
    tag_a = []
    tag_font = []
    for i, a in enumerate(div.select('a')):
        tag_a.append({
            'name': a.get('name'),
            'href': a.get('href')
        })
    for i, font in enumerate(div.select('font')):
        string = font.string
        if string is not None:
            tag_font.append(font.string.replace('\xa0', ' '))
    return(tag_a, tag_font)

def readTagA(content):
    return({
        'name': a.get('name'),
        'href': a.get('href')
    })


In [621]:
pd.read_csv('output/table002_body000-page005.txt')

Unnamed: 0                0                  1   2                  3  \
0           0              NaN                NaN NaN                NaN   
1           1              NaN                NaN NaN                NaN   
2           2              NaN  December 31, 2016 NaN  December 31, 2015   
3           3             GMNA              4,857 NaN                NaN   
4           4              GME              6,104 NaN                NaN   
5           5             GMIO              7,232 NaN                NaN   
6           6             GMSA              1,259 NaN                NaN   
7           7  Total worldwide             19,452 NaN                NaN   

        4                  5   6       7   8  
0     NaN                NaN NaN     NaN NaN  
1     NaN                NaN NaN     NaN NaN  
2     NaN  December 31, 2014 NaN     NaN NaN  
3   4,886                NaN NaN   4,908 NaN  
4   6,330                NaN NaN   6,633 NaN  
5   7,755                NaN NaN   7,699 NaN  
6   1,281                NaN NaN   1,272 NaN  
7  20,252                NaN NaN  20,512 NaN

In [585]:
font


<font style="font-family:inherit;font-size:10pt;"><br/></font>